# n-Pair Trident Scattering Process

In this file, we set up an n-pair trident scattering process. A trident
process looks like $k e^- \to e^- (e^- e^+)^n$.

You can download this file as a [jupyter notebook](trident.ipynb).

In [1]:
using QEDFeynmanDiagrams

We need some of the packages of the [QEDjl-project](https://github.com/QEDjl-project) for base
functionality and the `ScatteringProcess` type.

In [2]:
using QEDcore
using QEDprocesses

Let's decide how many pairs our trident should produce:

In [3]:
n = 2;

Now we setup the scattering process accordingly. We only consider a single spin/polarization
combination here. For an example with many spin and polarization combinations, refer to the
[n-photon Compton example](compton.md)

In [4]:
proc = ScatteringProcess(
    (Electron(), Photon()),                                                         # incoming particles
    (Electron(), ntuple(_ -> Electron(), n)..., ntuple(_ -> Positron(), n)...),     # outgoing particles
    (SpinUp(), PolX()),                                                             # incoming particle spin/pols
    (SpinUp(), ntuple(_ -> SpinUp(), 2 * n)...),                                    # outgoing particle spin/pols
)

generic QED process
    incoming: electron (spin up), photon (x-polarized)
    outgoing: electron (spin up), electron (spin up), electron (spin up), positron (spin up), positron (spin up)


The `feynman_diagrams` function returns an iterator for all possible Feynman diagrams
for this scattering process. With its `length` overload, we can check how many diagrams
there are.

In [5]:
length(feynman_diagrams(proc))

252

Next, we can generate the DAG representing the computation for our scattering process'
squared matrix element. This uses `ComputableDAGs.jl`.

In [6]:
dag = graph(proc)

Graph:
  Nodes: Total: 619, QEDFeynmanDiagrams.ComputeTask_PropagatePairs: 42, QEDFeynmanDiagrams.ComputeTask_CollectTriples: 1, 
         QEDFeynmanDiagrams.ComputeTask_Triple: 81, QEDFeynmanDiagrams.ComputeTask_BaseState: 7, QEDFeynmanDiagrams.ComputeTask_CollectPairs: 42, 
         QEDFeynmanDiagrams.ComputeTask_Propagator: 42, ComputableDAGs.DataTask: 334, QEDFeynmanDiagrams.ComputeTask_Pair: 69, 
         QEDFeynmanDiagrams.ComputeTask_SpinPolCumulation: 1
  Edges: 950
  Total Compute Effort: 0.0
  Total Data Transfer: 0.0
  Total Compute Intensity: 0.0


To continue, we will need [`ComputableDAGs.jl`](https://github.com/ComputableDAGs/ComputableDAGs.jl). Since `ComputableDAGs.jl` uses
`RuntimeGeneratedFunction`s as the return type of `ComputableDAGs.get_compute_function`, we need
to initialize it in our current module.

In [7]:
using ComputableDAGs
using RuntimeGeneratedFunctions
RuntimeGeneratedFunctions.init(@__MODULE__)

With the DAG, the process, and `RuntimeGeneratedFunctions` initalized,
we can now generate the actual computable function:

In [8]:
func = get_compute_function(dag, proc, cpu_st(), @__MODULE__);

Now we need an input for the function, which is a `QEDcore.PhaseSpacePoint`.
For now, we generate random momenta for every particle. In the future, QEDevents
will be able to generate physical `PhaseSpacePoint`s.

In [9]:
psp = PhaseSpacePoint(
    proc,
    PerturbativeQED(),
    PhasespaceDefinition(SphericalCoordinateSystem(), ElectronRestFrame()),
    tuple((rand(SFourMomentum) for _ in 1:number_incoming_particles(proc))...),
    tuple((rand(SFourMomentum) for _ in 1:number_outgoing_particles(proc))...),
)

PhaseSpacePoint:
    process: generic QED process "ek -> eeepp"
    model: perturbative QED
    phasespace definition: spherical coordinates in electron rest frame
    incoming particles:
     -> incoming electron: [0.6090808121465816, 0.9145002254570902, 0.3599428801347099, 0.6990714737389248]
     -> incoming photon: [0.8226383561673087, 0.9359915251990777, 0.34032377617720355, 0.8015259617140802]
    outgoing particles:
     -> outgoing electron: [0.24014403669348228, 0.5166766306623721, 0.8135673483909858, 0.7611021656200303]
     -> outgoing electron: [0.18595204083815697, 0.1985891419018816, 0.1692913433841362, 0.7352293285217253]
     -> outgoing electron: [0.07132667337164755, 0.39273873360496825, 0.7118911136478124, 0.29643949594701247]
     -> outgoing positron: [0.11342556298105766, 0.7249291890841695, 0.49155127578767865, 0.9885378150606744]
     -> outgoing positron: [0.17793188440746732, 0.4144832374282976, 0.2236651228106329, 0.5828499858347936]


Finally, we can test that the function actually runs and computes something by
simply calling it on the `PhaseSpacePoint`:

In [10]:
func(psp)

0.07765089984945862

If we want, we can benchmark the execution speed too:

In [11]:
using BenchmarkTools
@benchmark func($psp)

BenchmarkTools.Trial: 10000 samples with 1 evaluation.
 Range (min … max):  13.254 μs …  44.743 μs  ┊ GC (min … max): 0.00% … 0.00%
 Time  (median):     13.455 μs               ┊ GC (median):    0.00%
 Time  (mean ± σ):   13.566 μs ± 970.005 ns  ┊ GC (mean ± σ):  0.00% ± 0.00%

   ▅▇█▇▆▃▁▁                                                    ▂
  ███████████▆▆▁▅▆▇█▇▆▆▅▃▄▄▃▄▄▃▄▄▄▁▄▄▅▃▁▄▄▄▃▄▁▁▁▄▄▃▅▄▁▄▄▁▄▄▁▄▄ █
  13.3 μs       Histogram: log(frequency) by time      16.6 μs <

 Memory estimate: 256 bytes, allocs estimate: 2.

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*